<a href="https://colab.research.google.com/github/mboman00/TutoringLily/blob/main/mmaction2_tutorial.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# MMAction2 Tutorial

Welcome to MMAction2! This is the official colab tutorial for using MMAction2. In this tutorial, you will learn
- Perform inference with a MMAction2 recognizer.
- Train a new recognizer with a new dataset.
- Perform spatio-temporal detection.

Let's start!

## Install MMAction2

In [1]:
# Check nvcc version
!nvcc -V
# Check GCC version
!gcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2015 NVIDIA Corporation
Built on Tue_Aug_11_14:27:32_CDT_2015
Cuda compilation tools, release 7.5, V7.5.17
gcc (Ubuntu 5.4.0-6ubuntu1~16.04.12) 5.4.0 20160609
Copyright (C) 2015 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.



In [2]:
# install dependencies: (use cu111 becudatoolkit=11.0cause colab has CUDA 11.1)
#pip install torch==1.9.1+cu111 torchvision==0.10.1+cu111 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch==1.9.0+cu111 torchvision==0.10.0+cu111 -f https://download.pytorch.org/whl/torch_stable.html


Looking in links: https://download.pytorch.org/whl/torch_stable.html
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 GB 424.5 kB/s eta 0:00:000:01m00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.1/23.1 MB 31.1 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 18.0 MB/s eta 0:00:0000:0100:01


In [3]:
# install mmcv-full thus we could use CUDA operators
!pip install mmcv-full -f https://download.openmmlab.com/mmcv/dist/cu111/torch1.9.0/index.html

# Install mmaction2
!rm -rf mmaction2
!git clone https://github.com/open-mmlab/mmaction2.git
%cd mmaction2

!pip install -e .

# Install some optional requirements
!pip install -r requirements/optional.txt

Looking in links: https://download.openmmlab.com/mmcv/dist/cu111/torch1.9.0/index.html
  Using cached https://download.openmmlab.com/mmcv/dist/cu111/torch1.9.0/mmcv_full-1.7.1-cp39-cp39-manylinux1_x86_64.whl (49.7 MB)
  Using cached opencv_python-4.7.0.72-cp37-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (61.8 MB)
  Using cached yapf-0.32.0-py2.py3-none-any.whl (190 kB)
  Using cached addict-2.4.0-py3-none-any.whl (3.8 kB)
Cloning into 'mmaction2'...
remote: Enumerating objects: 20649, done.
remote: Counting objects: 100% (179/179), done.
remote: Compressing objects: 100% (164/164), done.
remote: Total 20649 (delta 37), reused 92 (delta 9), pack-reused 20470
Receiving objects: 100% (20649/20649), 68.26 MiB | 19.87 MiB/s, done.
Resolving deltas: 100% (14599/14599), done.
Checking connectivity... done.
/home/mboman/projects/lily/TutoringLily/mmaction2
Obtaining file:///home/mboman/projects/lily/TutoringLily/mmaction2
  Preparing metadata (setup.py) ... done
  Using cached decord-0

In [4]:
# Check Pytorch installation
import torch, torchvision
print(torch.__version__, torch.cuda.is_available())

# Check MMAction2 installation
import mmaction
print(mmaction.__version__)

# Check MMCV installation
from mmcv.ops import get_compiling_cuda_version, get_compiler_version
print(get_compiling_cuda_version())
print(get_compiler_version())

/home/mboman/miniconda3/envs/lily/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


1.9.0+cu111 True
0.24.1
11.1
GCC 7.3


/home/mboman/miniconda3/envs/lily/lib/python3.9/site-packages/mmcv/__init__.py:20: UserWarning: On January 1, 2023, MMCV will release v2.0.0, in which it will remove components related to the training process and add a data transformation module. In addition, it will rename the package names mmcv to mmcv-lite and mmcv-full to mmcv. See https://github.com/open-mmlab/mmcv/blob/master/docs/en/compatibility.md for more details.
  warnings.warn(


## Perform inference with a MMAction2 recognizer
MMAction2 already provides high level APIs to do inference and training.

In [5]:
!mkdir checkpoints
!wget -c https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth \
      -O checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth

--2023-03-16 16:08:13--  https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
Resolving download.openmmlab.com (download.openmmlab.com)... 8.45.176.208, 8.45.176.210, 8.45.176.211, ...
Connecting to download.openmmlab.com (download.openmmlab.com)|8.45.176.208|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 97579339 (93M) [application/octet-stream]
Saving to: ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’

checkpoints/tsn_r50 100%[===================>]  93.06M  22.0MB/s    in 4.1s    

2023-03-16 16:08:17 (22.6 MB/s) - ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’ saved [97579339/97579339]



In [6]:
#!cd mmaction2
import torch

SyntaxError: invalid syntax (1162304072.py, line 1)

In [7]:
from mmaction.apis import inference_recognizer, init_recognizer

# Choose to use a config and initialize the recognizer
config = 'configs/recognition/tsn/tsn_r50_video_inference_1x1x3_100e_kinetics400_rgb.py'
# Setup a checkpoint file to load
checkpoint = 'checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'
# Initialize the recognizer
model = init_recognizer(config, checkpoint, device='cuda:0')

load checkpoint from local path: checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth


In [8]:
# Use the recognizer to do inference
video = 'demo/demo.mp4'
label = 'tools/data/kinetics/label_map_k400.txt'
results = inference_recognizer(model, video)

labels = open(label).readlines()
labels = [x.strip() for x in labels]
results = [(labels[k[0]], k[1]) for k in results]

/home/mboman/miniconda3/envs/lily/lib/python3.9/site-packages/torch/nn/functional.py:718: UserWarning: Named tensors and all their associated APIs are an experimental feature and subject to change. Please do not use them for anything important until they are released as stable. (Triggered internally at  /pytorch/c10/core/TensorImpl.h:1156.)
  return torch.max_pool2d(input, kernel_size, stride, padding, dilation, ceil_mode)


In [9]:
# Let's show the results
for result in results:
    print(f'{result[0]}: ', result[1])

arm wrestling:  29.616438
rock scissors paper:  10.75484
shaking hands:  9.9084
clapping:  9.189912
massaging feet:  8.305306


## Train a recognizer on customized dataset

To train a new recognizer, there are usually three things to do:
1. Support a new dataset
2. Modify the config
3. Train a new recognizer

### Support a new dataset

In this tutorial, we gives an example to convert the data into the format of existing datasets. Other methods and more advanced usages can be found in the [doc](/docs/en/tutorials/new_dataset.md)

Firstly, let's download a tiny dataset obtained from [Kinetics-400](https://deepmind.com/research/open-source/open-source-datasets/kinetics/). We select 30 videos with their labels as train dataset and 10 videos with their labels as test dataset.

In [10]:
# download, decompress the data
!rm kinetics400_tiny.zip*
!rm -rf kinetics400_tiny
!wget https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
!unzip kinetics400_tiny.zip > /dev/null

rm: cannot remove 'kinetics400_tiny.zip*': No such file or directory
--2023-03-16 16:09:01--  https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
Resolving download.openmmlab.com (download.openmmlab.com)... 8.45.176.208, 8.45.176.210, 8.45.176.211, ...
Connecting to download.openmmlab.com (download.openmmlab.com)|8.45.176.208|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 18308682 (17M) [application/zip]
Saving to: ‘kinetics400_tiny.zip’

kinetics400_tiny.zi 100%[===================>]  17.46M  18.0MB/s    in 1.0s    

2023-03-16 16:09:02 (18.0 MB/s) - ‘kinetics400_tiny.zip’ saved [18308682/18308682]



In [11]:
# Check the directory structure of the tiny data

# Install tree first
#!apt-get -q install tree
!tree kinetics400_tiny

kinetics400_tiny
├── kinetics_tiny_train_video.txt
├── kinetics_tiny_val_video.txt
├── train
│   ├── 27_CSXByd3s.mp4
│   ├── 34XczvTaRiI.mp4
│   ├── A-wiliK50Zw.mp4
│   ├── D32_1gwq35E.mp4
│   ├── D92m0HsHjcQ.mp4
│   ├── DbX8mPslRXg.mp4
│   ├── FMlSTTpN3VY.mp4
│   ├── h10B9SVE-nk.mp4
│   ├── h2YqqUhnR34.mp4
│   ├── iRuyZSKhHRg.mp4
│   ├── IyfILH9lBRo.mp4
│   ├── kFC3KY2bOP8.mp4
│   ├── LvcFDgCAXQs.mp4
│   ├── O46YA8tI530.mp4
│   ├── oMrZaozOvdQ.mp4
│   ├── oXy-e_P_cAI.mp4
│   ├── P5M-hAts7MQ.mp4
│   ├── phDqGd0NKoo.mp4
│   ├── PnOe3GZRVX8.mp4
│   ├── R8HXQkdgKWA.mp4
│   ├── RqnKtCEoEcA.mp4
│   ├── soEcZZsBmDs.mp4
│   ├── TkkZPZHbAKA.mp4
│   ├── T_TMNGzVrDk.mp4
│   ├── WaS0qwP46Us.mp4
│   ├── Wh_YPQdH1Zg.mp4
│   ├── WWP5HZJsg-o.mp4
│   ├── xGY2dP0YUjA.mp4
│   ├── yLC9CtWU5ws.mp4
│   └── ZQV4U2KQ370.mp4
└── val
    ├── 0pVGiAU6XEA.mp4
    ├── AQrbRSnRt8M.mp4
    ├── b6Q_b7vgc7Q.mp4
    ├── ddvJ6-faICE.mp4
    ├── IcLztCtvhb8.mp4
    ├── ik4BW3-SCts.mp4
    ├── jqRrH30V0k4.mp4
    ├── SU_

In [12]:
# After downloading the data, we need to check the annotation format
!cat kinetics400_tiny/kinetics_tiny_train_video.txt

D32_1gwq35E.mp4 0
iRuyZSKhHRg.mp4 1
oXy-e_P_cAI.mp4 0
34XczvTaRiI.mp4 1
h2YqqUhnR34.mp4 0
O46YA8tI530.mp4 0
kFC3KY2bOP8.mp4 1
WWP5HZJsg-o.mp4 1
phDqGd0NKoo.mp4 1
yLC9CtWU5ws.mp4 0
27_CSXByd3s.mp4 1
IyfILH9lBRo.mp4 1
T_TMNGzVrDk.mp4 1
TkkZPZHbAKA.mp4 0
PnOe3GZRVX8.mp4 1
soEcZZsBmDs.mp4 1
FMlSTTpN3VY.mp4 1
WaS0qwP46Us.mp4 0
A-wiliK50Zw.mp4 1
oMrZaozOvdQ.mp4 1
ZQV4U2KQ370.mp4 0
DbX8mPslRXg.mp4 1
h10B9SVE-nk.mp4 1
P5M-hAts7MQ.mp4 0
R8HXQkdgKWA.mp4 0
D92m0HsHjcQ.mp4 0
RqnKtCEoEcA.mp4 0
LvcFDgCAXQs.mp4 0
xGY2dP0YUjA.mp4 0
Wh_YPQdH1Zg.mp4 0


According to the format defined in [`VideoDataset`](./datasets/video_dataset.py), each line indicates a sample video with the filepath and label, which are split with a whitespace.

### Modify the config

In the next step, we need to modify the config for the training.
To accelerate the process, we finetune a recognizer using a pre-trained recognizer.

In [13]:
from mmcv import Config
config113 = './configs/recognition/tsn/tsn_r50_video_320p_1x1x3_100e_kinetics400_rgb.py'

#cfg = Config.fromfile('./configs/recognition/tsn/tsn_r50_video_1x1x8_100e_kinetics400_rgb.py')
cfg = Config.fromfile(config113)

Given a config that trains a TSN model on kinetics400-full dataset, we need to modify some values to use it for training TSN on Kinetics400-tiny dataset.


In [14]:
from mmcv.runner import set_random_seed

# Modify dataset type and path
cfg.dataset_type = 'VideoDataset'
cfg.data_root = 'kinetics400_tiny/train/'
cfg.data_root_val = 'kinetics400_tiny/val/'
cfg.ann_file_train = 'kinetics400_tiny/kinetics_tiny_train_video.txt'
cfg.ann_file_val = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.ann_file_test = 'kinetics400_tiny/kinetics_tiny_val_video.txt'

cfg.data.test.type = 'VideoDataset'
cfg.data.test.ann_file = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.data.test.data_prefix = 'kinetics400_tiny/val/'

cfg.data.train.type = 'VideoDataset'
cfg.data.train.ann_file = 'kinetics400_tiny/kinetics_tiny_train_video.txt'
cfg.data.train.data_prefix = 'kinetics400_tiny/train/'

cfg.data.val.type = 'VideoDataset'
cfg.data.val.ann_file = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.data.val.data_prefix = 'kinetics400_tiny/val/'

# The flag is used to determine whether it is omnisource training
cfg.setdefault('omnisource', False)
# Modify num classes of the model in cls_head
cfg.model.cls_head.num_classes = 2
# We can use the pre-trained TSN model
cfg.load_from = './checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'

# Set up working dir to save files and logs.
cfg.work_dir = './tutorial_exps'

# The original learning rate (LR) is set for 8-GPU training.
# We divide it by 8 since we only use one GPU.
cfg.data.videos_per_gpu = cfg.data.videos_per_gpu // 16
cfg.optimizer.lr = cfg.optimizer.lr / 8 / 16
cfg.total_epochs = 10

# We can set the checkpoint saving interval to reduce the storage cost
cfg.checkpoint_config.interval = 5
# We can set the log print interval to reduce the the times of printing log
cfg.log_config.interval = 5

# Set seed thus the results are more reproducible
cfg.seed = 0
set_random_seed(0, deterministic=False)
cfg.gpu_ids = range(1)

# Save the best
cfg.evaluation.save_best='auto'


# We can initialize the logger for training and have a look
# at the final config used for training
print(f'Config:\n{cfg.pretty_text}')


Config:
model = dict(
    type='Recognizer2D',
    backbone=dict(
        type='ResNet',
        pretrained='torchvision://resnet50',
        depth=50,
        norm_eval=False),
    cls_head=dict(
        type='TSNHead',
        num_classes=2,
        in_channels=2048,
        spatial_type='avg',
        consensus=dict(type='AvgConsensus', dim=1),
        dropout_ratio=0.4,
        init_std=0.01),
    train_cfg=None,
    test_cfg=dict(average_clips=None))
optimizer = dict(type='SGD', lr=7.8125e-05, momentum=0.9, weight_decay=0.0001)
optimizer_config = dict(grad_clip=dict(max_norm=40, norm_type=2))
lr_config = dict(policy='step', step=[40, 80])
total_epochs = 10
checkpoint_config = dict(interval=5)
log_config = dict(interval=5, hooks=[dict(type='TextLoggerHook')])
dist_params = dict(backend='nccl')
log_level = 'INFO'
load_from = './checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'
resume_from = None
workflow = [('train', 1)]
opencv_num_threads = 0
mp_start_method = '

### Train a new recognizer

Finally, lets initialize the dataset and recognizer, then train a new recognizer!

In [15]:
import os.path as osp

from mmaction.datasets import build_dataset
from mmaction.models import build_model
from mmaction.apis import train_model

import mmcv

# Build the dataset"
datasets = [build_dataset(cfg.data.train)]

# Build the recognizer
model = build_model(cfg.model, train_cfg=cfg.get('train_cfg'), test_cfg=cfg.get('test_cfg'))

# Create work_dir
mmcv.mkdir_or_exist(osp.abspath(cfg.work_dir))
train_model(model, datasets, cfg, distributed=False, validate=True)

load checkpoint from torchvision path: torchvision://resnet50


2023-03-16 16:09:20,028 - mmaction - INFO - These parameters in pretrained checkpoint are not loaded: {'fc.weight', 'fc.bias'}
2023-03-16 16:09:20,134 - mmaction - INFO - load checkpoint from local path: ./checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
2023-03-16 16:09:20,270 - mmaction - WARNING - The model and loaded state dict do not match exactly

size mismatch for cls_head.fc_cls.weight: copying a param with shape torch.Size([400, 2048]) from checkpoint, the shape in current model is torch.Size([2, 2048]).
size mismatch for cls_head.fc_cls.bias: copying a param with shape torch.Size([400]) from checkpoint, the shape in current model is torch.Size([2]).
2023-03-16 16:09:20,272 - mmaction - INFO - Start running, host: mboman@mboman-PC, work_dir: /home/mboman/projects/lily/TutoringLily/mmaction2/tutorial_exps
2023-03-16 16:09:20,272 - mmaction - INFO - Hooks will be executed in the following order:
before_run:
(VERY_HIGH   ) StepLrUpdaterHook                  
(

[                                                  ] 0/10, elapsed: 0s, ETA:

[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)
[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)


[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 14.2 task/s, elapsed: 1s, ETA:     0s

2023-03-16 16:09:40,033 - mmaction - INFO - Evaluating top_k_accuracy ...
2023-03-16 16:09:40,035 - mmaction - INFO - 
top1_acc	0.8000
top5_acc	1.0000
2023-03-16 16:09:40,035 - mmaction - INFO - Evaluating mean_class_accuracy ...
2023-03-16 16:09:40,037 - mmaction - INFO - 
mean_acc	0.8000
2023-03-16 16:09:40,419 - mmaction - INFO - Now best checkpoint is saved as best_top1_acc_epoch_5.pth.
2023-03-16 16:09:40,420 - mmaction - INFO - Best top1_acc is 0.8000 at 5 epoch.
2023-03-16 16:09:40,421 - mmaction - INFO - Epoch(val) [5][5]	top1_acc: 0.8000, top5_acc: 1.0000, mean_class_accuracy: 0.8000
[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)
[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)
2023-03-16 16:09:43,274 - mmaction - INFO - Epoch [6][5/15]	lr: 7.813e-05, eta: 0:00:18, time: 0.569, data_time: 0.484, memory: 2918, top1_acc: 0.4000, top5_acc: 1.0000, loss_cls: 0.6654, loss: 0.6654, grad

[                                                  ] 0/10, elapsed: 0s, ETA:

[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)
[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)


[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 13.5 task/s, elapsed: 1s, ETA:     0s

2023-03-16 16:09:59,898 - mmaction - INFO - Evaluating top_k_accuracy ...
2023-03-16 16:09:59,900 - mmaction - INFO - 
top1_acc	0.8000
top5_acc	1.0000
2023-03-16 16:09:59,901 - mmaction - INFO - Evaluating mean_class_accuracy ...
2023-03-16 16:09:59,902 - mmaction - INFO - 
mean_acc	0.8000
2023-03-16 16:09:59,902 - mmaction - INFO - Epoch(val) [10][5]	top1_acc: 0.8000, top5_acc: 1.0000, mean_class_accuracy: 0.8000


### Understand the log
From the log, we can have a basic understanding the training process and know how well the recognizer is trained.

Firstly, the ResNet-50 backbone pre-trained on ImageNet is loaded, this is a common practice since training from scratch is more cost. The log shows that all the weights of the ResNet-50 backbone are loaded except the `fc.bias` and `fc.weight`.

Second, since the dataset we are using is small, we loaded a TSN model and finetune it for action recognition.
The original TSN is trained on original Kinetics-400 dataset which contains 400 classes but Kinetics-400 Tiny dataset only have 2 classes. Therefore, the last FC layer of the pre-trained TSN for classification has different weight shape and is not used.

Third, after training, the recognizer is evaluated by the default evaluation. The results show that the recognizer achieves 100% top1 accuracy and 100% top5 accuracy on the val dataset,
 
Not bad!

In [16]:
import torch
torch.cuda.empty_cache()

## Test the trained recognizer

After finetuning the recognizer, let's check the prediction results!

In [17]:
from mmaction.apis import single_gpu_test
from mmaction.datasets import build_dataloader
from mmcv.parallel import MMDataParallel

# Build a test dataloader
dataset = build_dataset(cfg.data.test, dict(test_mode=True))
data_loader = build_dataloader(
        dataset,
        videos_per_gpu=1,
        workers_per_gpu=cfg.data.workers_per_gpu,
        dist=False,
        shuffle=False)
model = MMDataParallel(model, device_ids=[0])
outputs = single_gpu_test(model, data_loader)

eval_config = cfg.evaluation
eval_config.pop('interval')
eval_res = dataset.evaluate(outputs, **eval_config)
for name, val in eval_res.items():
    print(f'{name}: {val:.04f}')

[                                                  ] 0/10, elapsed: 0s, ETA:

[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)
[W pthreadpool-cpp.cc:90] Warning: Leaking Caffe2 thread-pool after fork. (function pthreadpool)


[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 2.8 task/s, elapsed: 4s, ETA:     0s
Evaluating top_k_accuracy ...

top1_acc	0.8000
top5_acc	1.0000

Evaluating mean_class_accuracy ...

mean_acc	0.8000
top1_acc: 0.8000
top5_acc: 1.0000
mean_class_accuracy: 0.8000


/home/mboman/projects/lily/TutoringLily/mmaction2/mmaction/datasets/base.py:166: UserWarning: Option arguments for metrics has been changed to `metric_options`, See 'https://github.com/open-mmlab/mmaction2/pull/286' for more details
  warnings.warn(


## Perform Spatio-Temporal Detection
Here we first install MMDetection.

In [18]:
# Git clone mmdetection repo
%cd ..
!git clone https://github.com/open-mmlab/mmdetection.git
%cd mmdetection

# install mmdet
!pip install -e .
%cd ../mmaction2

/home/mboman/projects/lily/TutoringLily
fatal: destination path 'mmdetection' already exists and is not an empty directory.
/home/mboman/projects/lily/TutoringLily/mmdetection
Obtaining file:///home/mboman/projects/lily/TutoringLily/mmdetection
  Preparing metadata (setup.py) ... done
  Using cached pycocotools-2.0.6.tar.gz (24 kB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached terminaltables-3.1.10-py2.py3-none-any.whl (15 kB)
  Created wheel for pycocotools: filename=pycocotools-2.0.6-cp39-cp39-linux_x86_64.whl size=95671 sha256=a9e04036fbe486495029b4cb36cf6f2d2af49499e0eb0e07475ec391ba0af938
  Stored in directory: /home/mboman/.cache/pip/wheels/2f/58/25/e78f1f766e904a9071266661d20d0bc6644df86bcd160aba11
Successfully built pycocotools
  Running setup.py develop for mmdet
/home/mboman/projects/lily/TutoringLily/mmaction2


Download a video to `demo` directory in MMAction2.

In [20]:
!wget https://download.openmmlab.com/mmaction/dataset/sample/1j20qq1JyX4.mp4 -O demo/1j20qq1JyX4.mp4

--2023-03-16 16:11:43--  https://download.openmmlab.com/mmaction/dataset/sample/1j20qq1JyX4.mp4
Resolving download.openmmlab.com (download.openmmlab.com)... 8.45.176.212, 8.45.176.210, 8.45.176.207, ...
Connecting to download.openmmlab.com (download.openmmlab.com)|8.45.176.212|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4864186 (4.6M) [video/mp4]
Saving to: ‘demo/1j20qq1JyX4.mp4’

demo/1j20qq1JyX4.mp 100%[===================>]   4.64M  27.5MB/s    in 0.2s    

2023-03-16 16:11:43 (27.5 MB/s) - ‘demo/1j20qq1JyX4.mp4’ saved [4864186/4864186]



Run spatio-temporal demo.

In [45]:
%cd mmaction2
!python demo/demo_spatiotemporal_det.py --video demo/1j20qq1JyX4.mp4
%cd ..

/home/mboman/projects/lily/TutoringLily/mmaction2
/home/mboman/miniconda3/envs/lily/lib/python3.9/site-packages/mmcv/__init__.py:20: UserWarning: On January 1, 2023, MMCV will release v2.0.0, in which it will remove components related to the training process and add a data transformation module. In addition, it will rename the package names mmcv to mmcv-lite and mmcv-full to mmcv. See https://github.com/open-mmlab/mmcv/blob/master/docs/en/compatibility.md for more details.
  warnings.warn(
MBDEBUG ./tmp/1j20qq1JyX4
MBDEBUG ./tmp/1j20qq1JyX4/img_{:06d}.jpg
MBDEBUG < cv2.VideoCapture 0x7f9f2675fc30>
MBDEBUG: True [[[2 2 2]
  [2 2 2]
  [2 2 2]
  ...
  [0 3 1]
  [0 3 1]
  [0 3 1]]

 [[2 2 2]
  [2 2 2]
  [2 2 2]
  ...
  [0 3 1]
  [0 3 1]
  [0 3 1]]

 [[2 2 2]
  [2 2 2]
  [2 2 2]
  ...
  [0 3 1]
  [0 3 1]
  [0 3 1]]

 ...

 [[0 0 0]
  [0 0 0]
  [0 0 0]
  ...
  [9 0 1]
  [9 0 1]
  [9 0 1]]

 [[0 0 0]
  [0 0 0]
  [0 0 0]
  ...
  [9 0 1]
  [9 0 1]
  [9 0 1]]

 [[0 0 0]
  [0 0 0]
  [0 0 0]
  ...

In [22]:
# Check the video
from IPython.display import HTML
from base64 import b64encode
mp4 = open('mmaction2/demo/stdet_demo.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [52]:
#MBDEBUG opencv2
import cv2

In [73]:
vid = cv2.VideoCapture("test1/out.mp4")
flag, frame = vid.read()
print(flag)

True


In [89]:
%cd mmaction2
!python demo/demo_spatiotemporal_det.py --video ../test1/out.mp4 --checkpoint {cfg.work_dir}/latest.pth --config {config}
%cd ..

/home/mboman/projects/lily/TutoringLily/mmaction2
/home/mboman/miniconda3/envs/lily/lib/python3.9/site-packages/mmcv/__init__.py:20: UserWarning: On January 1, 2023, MMCV will release v2.0.0, in which it will remove components related to the training process and add a data transformation module. In addition, it will rename the package names mmcv to mmcv-lite and mmcv-full to mmcv. See https://github.com/open-mmlab/mmcv/blob/master/docs/en/compatibility.md for more details.
  warnings.warn(
Traceback (most recent call last):
  File "/home/mboman/projects/lily/TutoringLily/mmaction2/demo/demo_spatiotemporal_det.py", line 426, in <module>
    main()
  File "/home/mboman/projects/lily/TutoringLily/mmaction2/demo/demo_spatiotemporal_det.py", line 303, in main
    val_pipeline = config.data.val.pipeline
  File "/home/mboman/miniconda3/envs/lily/lib/python3.9/site-packages/mmcv/utils/config.py", line 50, in __getattr__
    raise ex
AttributeError: 'ConfigDict' object has no attribute 'val'
/h

In [85]:
mp4 = open('mmaction2/demo/stdet_demo.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)